In [222]:
directory = "../../Datasets/lusa_news/"
import os

files = []
for filename in os.listdir(directory):
    if filename.endswith(".txt") and "en" not in filename:
        files.append(filename.split(".")[0])  
        
len(files)

117

In [223]:
file = files[0]
file

'lusa_1'

In [224]:
from brat_parser import get_entities_relations_attributes_groups

def parseBratFile(file):
    entities, relations, attributes, groups = get_entities_relations_attributes_groups(file)
    return entities, relations, attributes, groups


def filter_annotations(annotations, type, match=False, exceptions=[]):
    if match:
        return {id: ann for id, ann in annotations.items() if type in ann.type and ann.type not in exceptions}
    else:
        return {id: ann for id, ann in annotations.items() if ann.type == type and ann.type not in exceptions}
    

def get_entities_translations(entities,entities_translations):
    res = {}
    for id_, entity in entities.items():
        entity.translation = entities_translations[id_].text
        res[id_] = entity
    return res

entities, relations, attributes, groups = get_entities_relations_attributes_groups(directory+ file + ".ann")

entities_translations, _, _, _ = get_entities_relations_attributes_groups(directory+ "translated_lusa/en/" + file + ".ann")

entities = get_entities_translations(entities,entities_translations)

In [225]:
entities

{'T24': Entity(id='T24', type='Participant', span=((108, 113),), text='A GNR'),
 'T42': Entity(id='T42', type='Participant', span=((156, 159),), text='bar'),
 'T25': Entity(id='T25', type='Participant', span=((163, 171),), text='Corotelo'),
 'T23': Entity(id='T23', type='Participant', span=((173, 205),), text='concelho de São Brás de Alportel'),
 'T27': Entity(id='T27', type='Participant', span=((218, 237),), text='cerca de 50 pessoas'),
 'T21': Entity(id='T21', type='Participant', span=((262, 272),), text='comunicado'),
 'T29': Entity(id='T29', type='Participant', span=((274, 295),), text='o Comando Territorial'),
 'T46': Entity(id='T46', type='Participant', span=((299, 303),), text='Faro'),
 'T30': Entity(id='T30', type='Participant', span=((307, 310),), text='GNR'),
 'T31': Entity(id='T31', type='Participant', span=((401, 415),), text='música ao vivo'),
 'T32': Entity(id='T32', type='Participant', span=((420, 446),), text='estabelecimento de bebidas'),
 'T33': Entity(id='T33', type=

In [226]:
directory+ file + ".ann"

'../../Datasets/lusa_news/lusa_1.ann'

In [227]:
entities

{'T24': Entity(id='T24', type='Participant', span=((108, 113),), text='A GNR'),
 'T42': Entity(id='T42', type='Participant', span=((156, 159),), text='bar'),
 'T25': Entity(id='T25', type='Participant', span=((163, 171),), text='Corotelo'),
 'T23': Entity(id='T23', type='Participant', span=((173, 205),), text='concelho de São Brás de Alportel'),
 'T27': Entity(id='T27', type='Participant', span=((218, 237),), text='cerca de 50 pessoas'),
 'T21': Entity(id='T21', type='Participant', span=((262, 272),), text='comunicado'),
 'T29': Entity(id='T29', type='Participant', span=((274, 295),), text='o Comando Territorial'),
 'T46': Entity(id='T46', type='Participant', span=((299, 303),), text='Faro'),
 'T30': Entity(id='T30', type='Participant', span=((307, 310),), text='GNR'),
 'T31': Entity(id='T31', type='Participant', span=((401, 415),), text='música ao vivo'),
 'T32': Entity(id='T32', type='Participant', span=((420, 446),), text='estabelecimento de bebidas'),
 'T33': Entity(id='T33', type=

In [228]:
def sentence_spans(file):
    spans = []
    start_index = 0 
    with open(file) as f:
        for line in f:
            end_index = start_index + len(line)
            spans.append((line, (start_index, end_index)))
            start_index = end_index
    return spans


    
def get_sentence_entities(span,entities):
    res = []
    for k, entity in entities.items():
        if entity.span[0][0] >= span[0] and entity.span[0][1] <= span[1]:
            res.append(entity)
    return res



def process_file(files):
    
    entries = {}
    for file in files:
        #print(file)
        entities, relations, attributes, groups = get_entities_relations_attributes_groups(directory+ file + ".ann")
        #print("parsed original")
        entities_translations, _, _, _ = get_entities_relations_attributes_groups(directory+ "translated_lusa/en/" + file + ".ann")
        entities = get_entities_translations(entities,entities_translations)
        #print("parsed translated")
        
        spans = sentence_spans(directory+ file + ".txt")

        spans_trasnlated = sentence_spans(directory+ "translated_lusa/en/" + file + ".txt")

        if len(spans) != len(spans_trasnlated):
            print("error")
        dict_sents = {}
        for i, (sentence, span) in enumerate(spans):
            dict_sents[span] = {
                "src_sent": sentence, 
                "src_anns": get_sentence_entities(span, entities),
                "tgt_sent": spans_trasnlated[i][0],
                "sent_tg_span": spans_trasnlated[i][1]
                }
        entry = {
            "sents": dict_sents,
            "entities": entities,
            "relations": list(relations.values()),
            "attributes": list(attributes.values()),
            "groups": list(groups.values())
        }
        entries[file] = entry
    return entries

entries = process_file(files)
len(entries)

117

In [229]:
from LinguAligner import AlignmentPipeline, translation

config= {
    "pipeline": [ "lemma", "M_Trans", "word_aligner","gestalt","leveinstein"], # can be changed according to the desired pipeline
    "spacy_model": "en_core_web_sm", # needed for lemma
    "WAligner_model": "bert-base-multilingual-uncased", # needed for word_aligner
}
aligner = AlignmentPipeline(config)

Loading spacy model: en_core_web_sm


c:\Users\Filip\AppData\Local\Programs\Python\Python39\lib\site-packages\spacy\util.py:887: UserWarning: [W095] Model 'en_core_web_sm' (3.2.0) was trained with spaCy v3.2 and may not be 100% compatible with the current version (3.5.4). If you see errors or degraded performance, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


Model loaded
Loading WAligner model: bert-base-multilingual-uncased
Model loaded


In [127]:

annotations = set()

for entry in entries:
    for span, sent in entry["sents"].items():
        for ann in sent["src_anns"]:
            annotations.add(ann.text)
print(len(annotations), annotations )

TypeError: string indices must be integers

In [66]:
lookupTable = {}

In [230]:
translator = translation.MicrosoftTranslator(source_lang="pt", target_lang="en", auth_key="f6d44239a73046ca8378bcdc689b395c")
for word in annotations:
    if word not in lookupTable and len(word) < 50:
        mtrans = translator.getMultipleTranslations(word)
        lookupTable[word] = mtrans
        print(word, mtrans)

In [231]:
#import json
#f_out = open("lookupTable_annotations.json", "w")
#json.dump(lookupTable, f_out, indent=4, ensure_ascii=False)
#f_out.flush()
#f_out.close()

import json
lookupTable = json.load(open("lookupTable_annotations.json"))

In [232]:
i = 0
for file, entry in entries.items():
    for span, sent in entry["sents"].items():
        for ann in sent["src_anns"]:
            target_annotation = aligner.align_annotation(sent["src_sent"], ann.text, sent["tgt_sent"], ann.translation, lookupTable=lookupTable, src_ann_start=ann.span[0][0])
            ann.tgt_ann = target_annotation
    i += 1
    print(i)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117


In [106]:
entries

[{'file': 'lusa_1',
  'sents': {(0, 21): {'src_sent': 'Redação, 11 out 2020\n',
    'src_anns': [Entity(id='T43', type='Time', span=((9, 20),), text='11 out 2020')],
    'tgt_sent': 'Editorial, October 11, 2020\n'},
   (21, 31): {'src_sent': 'VAM // JH\n',
    'src_anns': [],
    'tgt_sent': 'VAM // JH\n'},
   (31,
    108): {'src_sent': 'Covid-19: GNR acabou com festa ilegal com 50 pessoas em São Brás de Alportel\n', 'src_anns': [], 'tgt_sent': 'Covid-19: GNR ended illegal party with 50 people in São Brás de Alportel\n'},
   (108,
    259): {'src_sent': 'A GNR acabou no sábado com uma festa ilegal num bar em Corotelo, concelho de São Brás de Alportel, que reunia cerca de 50 pessoas, foi hoje anunciado.\n', 'src_anns': [Entity(id='T24', type='Participant', span=((108, 113),), text='A GNR'),
     Entity(id='T42', type='Participant', span=((156, 159),), text='bar'),
     Entity(id='T25', type='Participant', span=((163, 171),), text='Corotelo'),
     Entity(id='T23', type='Participant', s

In [233]:
from pickle import dump, load
#dump(entries, open("lusa_entries.pkl", "wb"))

### Data to Brat Format

In [234]:
entries = load(open("lusa_entries.pkl", "rb"))

In [236]:

for file, entry in entries.items():
    entry["entities"] = []
    for span, sent in entry["sents"].items():
        for ann in sent["src_anns"]:
            print(ann.text, ann.span, ann.translation, ann.tgt_ann)
            ann.text = ann.tgt_ann[0]
            ann.span = ((ann.tgt_ann[1][0] + sent["sent_tg_span"][0], ann.tgt_ann[1][1] + sent["sent_tg_span"][0] + 1),)
            entry["entities"].append(ann)

11, 2020 ((9, 20),) 11 Oct 2020 ('11, 2020', (19, 26))
A GNR ((108, 113),) The GNR ('the GNR', (13, 19))
bar ((156, 159),) Pub ('bar', (49, 51))
Corotelo ((163, 171),) Corotelo ('Corotelo', (56, 63))
concelho de São Brás de Alportel ((173, 205),) municipality of São Brás de Alportel ('municipality of São Brás de Alportel', (73, 108))
cerca de 50 pessoas ((218, 237),) around 50 people ('around 50 people', (134, 149))
o sábado ((122, 130),) the Saturday ('Saturday', (3, 10))
hoje ((243, 247),) today ('today', (169, 173))
num ((152, 155),) on one ('a', (156, 156))
em ((160, 162),) in ('in', (66, 67))
acabou ((114, 120),) he finished ('ended', (21, 25))
festa ilegal ((139, 151),) illegal party ('illegal party', (30, 42))
que ((207, 210),) what ('which', (111, 115))
reunia ((211, 217),) gathered ('brought', (117, 123))
anunciado ((248, 257),) announced ('announced', (159, 167))
comunicado ((262, 272),) statement ('statement', (5, 13))
o Comando Territorial ((274, 295),) the Territorial Comm

In [237]:
entries["lusa_1"]["entities"]

[Entity(id='T43', type='Time', span=((19, 27),), text='11, 2020'),
 Entity(id='T24', type='Participant', span=((124, 131),), text='the GNR'),
 Entity(id='T42', type='Participant', span=((160, 163),), text='bar'),
 Entity(id='T25', type='Participant', span=((167, 175),), text='Corotelo'),
 Entity(id='T23', type='Participant', span=((184, 220),), text='municipality of São Brás de Alportel'),
 Entity(id='T27', type='Participant', span=((245, 261),), text='around 50 people'),
 Entity(id='T2', type='Spatial_Relation', span=((114, 122),), text='Saturday'),
 Entity(id='T5', type='Time', span=((280, 285),), text='today'),
 Entity(id='T28', type='Spatial_Relation', span=((267, 268),), text='a'),
 Entity(id='T22', type='Spatial_Relation', span=((177, 179),), text='in'),
 Entity(id='T1', type='Event', span=((132, 137),), text='ended'),
 Entity(id='T3', type='Event', span=((141, 154),), text='illegal party'),
 Entity(id='T26', type='Event', span=((222, 227),), text='which'),
 Entity(id='T4', type=

In [238]:
#read a brat file, swap every entity with a new entity and write a new file with the new entities
def get_entity(id,entities):
    found = None
    res = 0
    for entity in entities:
        #print(entity.id, id)
        if entity.id == id:
            found =  entity
    if not found:

        print("not found")
    return found


def swap_entities(file, entry, output_file):
    with open(file) as f:
        with open(output_file, "w") as f_out:
            for line in f:
                if line.startswith("T"):
                    id = line.strip().split("\t")[0]
                    entity = get_entity(id, entry["entities"])
                    f_out.write(f"{entity.id}\t{entity.type} {entity.span[0][0]} {entity.span[0][1]}\t{entity.text}\n")
                    #print(entity.text)
                else:
                    f_out.write(line)
                    ...
                    
for file in files:
    swap_entities(directory + file + ".ann", entries[file], directory+ "translated_lusa/en_aligned/" + file + ".ann")

In [194]:
#copy text files crom translated_lusa/en to translated_lusa/en_aligned
import shutil
for file in files:
    shutil.copy(directory + "translated_lusa/en/" + file + ".txt", directory+ "translated_lusa/en_aligned/" + file + ".txt")

In [220]:
for file in files[0:1]:
    print(file)
    entities, relations, attributes, groups = get_entities_relations_attributes_groups(directory+ "translated_lusa/en_aligned/" +file + ".ann")
    print(entities)

    #print("parsed translated")

lusa_1
{'T24': Entity(id='T24', type='Participant', span=((121, 128),), text='the GNR'), 'T42': Entity(id='T42', type='Participant', span=((157, 160),), text='bar'), 'T25': Entity(id='T25', type='Participant', span=((164, 172),), text='Corotelo'), 'T23': Entity(id='T23', type='Participant', span=((181, 217),), text='municipality of São Brás de Alportel'), 'T27': Entity(id='T27', type='Participant', span=((242, 258),), text='around 50 people'), 'T21': Entity(id='T21', type='Participant', span=((264, 273),), text='statement'), 'T29': Entity(id='T29', type='Participant', span=((275, 303),), text='the Faro Territorial Command'), 'T46': Entity(id='T46', type='Participant', span=((279, 283),), text='Faro'), 'T30': Entity(id='T30', type='Participant', span=((311, 314),), text='GNR'), 'T31': Entity(id='T31', type='Participant', span=((389, 399),), text='live music'), 'T32': Entity(id='T32', type='Participant', span=((405, 427),), text='drinking establishment'), 'T33': Entity(id='T33', type='Pa